In [2]:
eventsPath = os.environ["YAHOO_DATA"]
rawEventsRdd = sc.textFile(eventsPath + "events.txt")
rawInstallsRdd = sc.textFile(eventsPath + "installs.txt")
rawMergedRdd = rawEventsRdd.union(rawInstallsRdd)
rawMergedRdd.take(3)

[u'001e6d8e-cbe7-4374-8c38-f37962a457e9\tair.com.smashatom.bingo\t1421009506\t47.237476\t-122.530884\tTacoma\t6\t12\tApp_Opened',
 u'001e6d8e-cbe7-4374-8c38-f37962a457e9\tcom.android.vending\t1421029924\t47.237476\t-122.530891\tTacoma\t6\t18\tApp_Opened',
 u'001e6d8e-cbe7-4374-8c38-f37962a457e9\tair.com.buffalo_studios.bingorush2\t1421015988\t47.237461\t-122.530899\tTacoma\t6\t14\tApp_Opened']

In [32]:
rawInstallsRdd.take(3)

[u'001e6d8e-cbe7-4374-8c38-f37962a457e9\tair.com.buffalo_studios.bingorush2\t1420974077\t47.237461\t-122.530907\tTacoma\t6\t3\tApp_Installed\tinstall',
 u'009ef415-eb39-4f3e-8714-2b22a6490fbb\tcom.pandora.android\t1421228526\t37.353397\t-121.944977\tSanta Clara\t2\t1\tApp_Installed\tinstall',
 u'01fb3e32-5e7f-498d-aa51-aa8eabdb12ac\tcom.fractal360.go.launcherex.theme.gfl\t1421543961\t33.842270\t-84.211357\tTucker\t5\t20\tApp_Installed\tinstall']

In [4]:
def parseRawData(line):
    lineSplit = line.split("\t")
    return (lineSplit[0], #userid
              lineSplit[1], #itemid
              int(lineSplit[2]), #ts
              float(lineSplit[3]), #lat
              float(lineSplit[4]), #lon
              lineSplit[5], #city
              int(lineSplit[6]), #day_of_week
              int(lineSplit[7]), #time_of_day
              lineSplit[-1]) #event_type
    

eventsRdd = rawMergedRdd.map(parseRawData).cache()
eventsRdd.take(3)

[(u'001e6d8e-cbe7-4374-8c38-f37962a457e9',
  u'air.com.smashatom.bingo',
  1421009506,
  47.237476,
  -122.530884,
  u'Tacoma',
  6,
  12,
  u'App_Opened'),
 (u'001e6d8e-cbe7-4374-8c38-f37962a457e9',
  u'com.android.vending',
  1421029924,
  47.237476,
  -122.530891,
  u'Tacoma',
  6,
  18,
  u'App_Opened'),
 (u'001e6d8e-cbe7-4374-8c38-f37962a457e9',
  u'air.com.buffalo_studios.bingorush2',
  1421015988,
  47.237461,
  -122.530899,
  u'Tacoma',
  6,
  14,
  u'App_Opened')]

In [5]:
userIdConversionDictionary = eventsRdd.map(lambda x: x[0]).distinct().zipWithIndex().collectAsMap()
userIdConversionDictionaryBroadcast = sc.broadcast(userIdConversionDictionary)
itemIdConversionDictionary = eventsRdd.map(lambda x: x[1]).distinct().zipWithIndex().collectAsMap()
itemIdConversionDictionaryBroadcast = sc.broadcast(itemIdConversionDictionary)
cityConversionDictionary = eventsRdd.map(lambda x: x[5]).distinct().zipWithIndex().collectAsMap()
cityConversionDictionaryBroadcast = sc.broadcast(cityConversionDictionary)

In [7]:
eventsConvertedRdd = eventsRdd.map(lambda x: (userIdConversionDictionaryBroadcast.value[x[0]],
    itemIdConversionDictionaryBroadcast.value[x[1]],
    x[2],
    x[3],
    x[4],
    cityConversionDictionaryBroadcast.value[x[5]],
    x[6],
    x[7],
    x[8]
    ))

eventsConvertedRdd.take(3)

[(4601, 6339, 1421009506, 47.237476, -122.530884, 8328, 6, 12, u'App_Opened'),
 (4601, 30092, 1421029924, 47.237476, -122.530891, 8328, 6, 18, u'App_Opened'),
 (4601, 98256, 1421015988, 47.237461, -122.530899, 8328, 6, 14, u'App_Opened')]

In [ ]:
eventsConvertedRdd.map(lambda eventRaw: (
    eventRaw.userId,eventRaw.itemId,eventRaw.ts,eventRaw.city,eventRaw.day_of_week,eventRaw.time_of_day,
    eventRaw.latitude,eventRaw.longitude)
        ).saveAsTextFile(eventsPath + "events_merged_parsed")

In [8]:
import json
with open(eventsPath + 'userIdConversionDictionaryMerged.txt', 'w') as outfile:
    json.dump(userIdConversionDictionary, outfile)
with open(eventsPath + 'itemIdConversionDictionaryMerged.txt', 'w') as outfile:
    json.dump(itemIdConversionDictionary, outfile)
with open(eventsPath + 'cityConversionDictionaryMerged.txt', 'w') as outfile:
    json.dump(cityConversionDictionary, outfile)

In [ ]:
def parseUserAppList(line):
    lineSplit = line.split("\t")
    return userIdConversionDictionary[lineSplit[0]],[itemIdConversionDictionary[app[1:-1]] for app in lineSplit[1][1:-1].split(",")]

appListRdd = rawAppListRdd.map(parseUserAppList)
appListMap = appListRdd.collectAsMap()
with open(eventsPath + '/userAppMap.txt', 'w') as outfile:
    json.dump(appListMap, outfile)
appListRdd.take(3)

# Format data into context information

In [ ]:
execfile("../script/utils.py")
#eventRDD = loadDataset(eventsPath + "events_parsed").groupBy(lambda x: x.userId).map(lambda (x,y): (x, sorted(list(y),key=lambda a: a.ts)))
#eventRDD = eventRDD.map(lambda x: (x[0], 
#                        map(lambda y : TrainRow(itemId=y.itemId, 
#                                               context = ContextRow(ts=y.ts,city=y.city,
#                                                                   lat=y.lat, lon=y.lon, moving = 1)), x[1])))
eventRDD = eventsConvertedRdd.groupBy(lambda x: x[0]).map(lambda (x,y): (x, sorted(list(y),key=lambda a: a[2])))
eventRDD.take(1)

In [19]:
def tempRemoveUserIdDup(line):
    data = line[1]
    newData = [el[1:] for el in data]
    return line[0], newData
eventRDD2 = eventRDD.map(tempRemoveUserIdDup)
eventRDD2.take(1)

[(0,
  [(30606, 1421405995, 29.840933, -95.532265, 4128, 4, 4, u'App_Opened'),
   (26351, 1421405998, 29.840933, -95.532265, 4128, 4, 4, u'App_Opened'),
   (11695, 1421406038, 29.840933, -95.532265, 4128, 4, 5, u'App_Opened'),
   (90028, 1421406046, 29.840933, -95.532265, 4128, 4, 5, u'App_Opened'),
   (90028, 1421406056, 29.840933, -95.532265, 4128, 4, 5, u'App_Opened'),
   (20646, 1421406099, 29.840933, -95.532265, 4128, 4, 5, u'App_Opened'),
   (20646, 1421406111, 29.840933, -95.532265, 4128, 4, 5, u'App_Opened'),
   (104640, 1421406115, 29.840933, -95.532265, 4128, 4, 5, u'App_Opened'),
   (82659, 1421406237, 29.840933, -95.532265, 4128, 4, 5, u'App_Opened'),
   (20646, 1421406259, 29.840933, -95.532265, 4128, 4, 5, u'App_Opened'),
   (65090, 1421406271, 29.840933, -95.532265, 4128, 4, 5, u'App_Opened'),
   (26351, 1421406281, 29.840933, -95.532265, 4128, 4, 5, u'App_Opened'),
   (59816, 1421406284, 29.840933, -95.532265, 4128, 4, 5, u'App_Opened'),
   (30092, 1421406295, 29.840933

In [31]:
eventRDD2 = eventRDD2.filter(lambda x : x if len(x[1]) > 10)

2

In [85]:
def detectMovement(line):
    #location clustering
    listGroup = map(lambda x: list(x), line[1])
    workGroup = [x for x in listGroup if datetime.datetime.fromtimestamp(int(x[1])).hour >= 6 and  
            datetime.datetime.fromtimestamp(int(x[1])).hour <= 18]
    numNearLocation = []
    i = 0
    for x in workGroup:
        numNearLocation.append(0);
        for y in workGroup:
            if haversine(x[3], x[2], y[3], y[2]) < 0.1:
                numNearLocation[i] = numNearLocation[i] + 1
        i = i + 1
    if len(numNearLocation) > 0:
        index_work = numNearLocation.index(max(numNearLocation))
    else:
        index_work = -1
    homeGroup = [x for x in listGroup if datetime.datetime.fromtimestamp(int(x[1])).hour < 6 or
            datetime.datetime.fromtimestamp(int(x[1])).hour > 18]
    numNearLocation = []
    i = 0
    for x in homeGroup:
        numNearLocation.append(0);
        for y in homeGroup:
            if haversine(x[3], x[2], y[3], y[2]) < 0.1:
                numNearLocation[i] = numNearLocation[i] + 1
        i = i + 1
    if len(numNearLocation) > 0:
        index_home = numNearLocation.index(max(numNearLocation))
    else:
        index_home = -1
    
    
    if (index_home != -1 and index_work != -1) and (index_home < len(homeGroup) and index_work < len(workGroup)) and (len(homeGroup) > 0 and len(workGroup)>0):
        listGroup = [(x[0],x[1],1) if haversine(x[3], x[2], workGroup[index_work][3], workGroup[index_work][2]) < 0.01
                 else( 
                    (x[0],x[1],2) if haversine(x[3], x[2], homeGroup[index_home][3], homeGroup[index_home][2]) < 0.01
                
                    else (x[0],x[1],3) 
                    )
                     
                 for x in listGroup]
    else:
        
        listGroup = [(x[0],x[1],3)
                     
                 for x in listGroup]
    listGroup = [(x[0],1) if datetime.datetime.fromtimestamp(int(x[1])).hour >= 6 and
                datetime.datetime.fromtimestamp(int(x[1])).hour <= 13
                    else(
                      (x[0],2) if datetime.datetime.fromtimestamp(int(x[1])).hour >= 13 and
                        datetime.datetime.fromtimestamp(int(x[1])).hour <= 18
                      else (x[0],3)
                    )
                for x in listGroup]
    #movement
    data = line[1]
    eventType = {'App_Opened': 0, 'install':1, 'uninstall': 2}
    #itemid, ts,lat,lon,city,dayofweek,timeofday,eventtype,movement,locationtype,partofday
 

    newData = [(data[0][0],data[0][1], data[0][2], data[0][3], data[0][4],data[0][5],data[0][6],
                eventType[data[0][7]], 1, listGroup[0][1],convertTime(data[0][1]) )]
    
    for i in xrange(1,len(data)):
            event = data[i]
            distance = haversine(event[3],event[2], data[i-1][3], data[i-1][2]) * 1000 #in meters
            time_difference = event[1] - newData[i-1][1] #in seconds
            moving = 1 #not available 
            if time_difference <= 300: #if 2 consecutive events are more than 300 seconds away, the movement is not available
                velocity =  distance/time_difference if time_difference > 0 else -1
                if velocity < 0:
                    moving = 1; #not available
                elif velocity >= 0 and velocity <= 1:
                    moving = 2  #standing still
                elif velocity <=2.4:
                    moving = 3 #walking spead
                else:
                    moving = 4 #faster
            newData.append((event[0],event[1],event[2],event[3],event[4],event[5],event[6],
                            eventType[event[7]], moving, listGroup[i][1], convertTime(event[1])))
    return (line[0], newData)
def filterInvalidLines(line):
    return len(line[1]) > 10 and len(line[1][7])==8 # just a random 8th element size check
eventRDD_context = eventRDD2.filter(filterInvalidLines).map(detectMovement)
eventRDD_context.take(100)
 #itemid, ts,lat,lon,city,dayofweek,timeofday,eventtype,movement,locationtype,partofday

[(0,
  [(30606, 1421405995, 29.840933, -95.532265, 4128, 4, 4, 0, 1, 1, 1),
   (26351, 1421405998, 29.840933, -95.532265, 4128, 4, 4, 0, 2, 1, 1),
   (11695, 1421406038, 29.840933, -95.532265, 4128, 4, 5, 0, 2, 1, 2),
   (90028, 1421406046, 29.840933, -95.532265, 4128, 4, 5, 0, 2, 1, 2),
   (90028, 1421406056, 29.840933, -95.532265, 4128, 4, 5, 0, 2, 1, 2),
   (20646, 1421406099, 29.840933, -95.532265, 4128, 4, 5, 0, 2, 1, 2),
   (20646, 1421406111, 29.840933, -95.532265, 4128, 4, 5, 0, 2, 1, 2),
   (104640, 1421406115, 29.840933, -95.532265, 4128, 4, 5, 0, 2, 1, 2),
   (82659, 1421406237, 29.840933, -95.532265, 4128, 4, 5, 0, 2, 1, 2),
   (20646, 1421406259, 29.840933, -95.532265, 4128, 4, 5, 0, 2, 1, 2),
   (65090, 1421406271, 29.840933, -95.532265, 4128, 4, 5, 0, 2, 1, 2),
   (26351, 1421406281, 29.840933, -95.532265, 4128, 4, 5, 0, 2, 1, 2),
   (59816, 1421406284, 29.840933, -95.532265, 4128, 4, 5, 0, 2, 1, 2),
   (30092, 1421406295, 29.840933, -95.532265, 4128, 4, 5, 0, 2, 1, 2),


In [ ]:
splitRatio = 0.8
def splitRddMerged(line):
    open_events = [el for el in line[1] if el[7] == 0]
    install_events = [el for el in line[1] if el[7] == 1]
    uninstall_events = [el for el in line[1] if el[7] == 2]
    num_open = len(open_events)
    split_amount = int(num_open*splitRatio)
    return line[0],open_events[:split_amount], open_events[split_amount:], install_events, uninstall_events
eventRDD_context.map(splitRddMerged).saveAsTextFile(eventsPath + "splitedDataMerged")

In [ ]:
eventsPath = os.environ["YAHOO_DATA"]
execfile("../script/utils.py")
splitedRdd = sc.textFile(eventsPath + "splitedData")
splitedRdd = splitedRdd.map(parseContextData2)

#(uid,[[train],[test]]

In [ ]:
splitedRddinstalls = sc.textFile(eventsPath + "splitedDataInstalled")
splitedRddinstalls = splitedRddinstalls.map(parseContextData2install)

In [ ]:
splitedRddinstalls.count(), splitedRdd.count()

In [ ]:
#deprecated
test_rdd = sc.textFile(eventsPath + "test")
test_rdd = test_rdd.map(parseContextData)
test_rdd.take(1)

In [ ]:
#deprecated
train_rdd = sc.textFile(eventsPath + "train")
train_rdd = train_rdd.map(parseContextData)
train_rdd.take(1)